In [1]:
import ccxt
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import ta

In [2]:
import ccxt
import pandas as pd
import time
import ta

symbol = "DOGE/USDT"
exchange_id = "binance"
ohlcv_timeframe = "1m"  # CCXT timeframe

def fetch_ohlcv(symbol, exchange_id, timeframe, since=None, limit=1000, max_bars=100000):
    exchange = getattr(ccxt, exchange_id)()
    exchange.load_markets()

    all_bars = []
    fetch_since = since if since else exchange.milliseconds() - (max_bars * 60 * 1000)  # Default: fetch last max_bars minutes

    while len(all_bars) < max_bars:
        try:
            new_bars = exchange.fetch_ohlcv(symbol, timeframe, since=fetch_since, limit=limit)

            if not new_bars:
                print("No new bars returned. Stopping...")
                break  # Stop if no new data is returned

            all_bars.extend(new_bars)  # Append new data
            print(f"Fetched {len(new_bars)} bars, Total: {len(all_bars)}")

            fetch_since = new_bars[-1][0] + 1  # Move `since` forward

            if len(new_bars) < limit:
                print("Last batch returned less than the limit. Likely at the end of data.")
                break  # Stop if no more data is available
            
            time.sleep(exchange.rateLimit / 1000)  # Avoid API rate limits
            
        except Exception as e:
            print(f"Error fetching data: {e}")
            break
    
    # Convert to DataFrame
    df = pd.DataFrame(all_bars, columns=['timestamp', 'open', 'high', 'low', 'close', 'volume'])
    df['timestamp'] = pd.to_datetime(df['timestamp'], unit='ms')
    
    # Add technical indicators
    df["SMA_20"] = ta.trend.sma_indicator(df["close"], window=20)  # 20-period SMA
    df["SMA_50"] = ta.trend.sma_indicator(df["close"], window=50)  # 50-period SMA
    df["EMA_20"] = ta.trend.ema_indicator(df["close"], window=20)  # 20-period EMA
    df["RSI_14"] = ta.momentum.rsi(df["close"], window=14)  # RSI (Relative Strength Index)
    df["MACD"] = ta.trend.macd(df["close"])  # MACD Line
    df["MACD_Signal"] = ta.trend.macd_signal(df["close"])  # MACD Signal Line
    df["ATR_14"] = ta.volatility.average_true_range(df["high"], df["low"], df["close"], window=14)  # ATR
    
    df.dropna(inplace=True)
    
    print(f"Final data count: {len(df)} bars")
    return df

# Example usage:
df = fetch_ohlcv(symbol, exchange_id, ohlcv_timeframe, max_bars=100000)

Fetched 1000 bars, Total: 1000
Fetched 1000 bars, Total: 2000
Fetched 1000 bars, Total: 3000
Fetched 1000 bars, Total: 4000
Fetched 1000 bars, Total: 5000
Fetched 1000 bars, Total: 6000
Fetched 1000 bars, Total: 7000
Fetched 1000 bars, Total: 8000
Fetched 1000 bars, Total: 9000
Fetched 1000 bars, Total: 10000
Fetched 1000 bars, Total: 11000
Fetched 1000 bars, Total: 12000
Fetched 1000 bars, Total: 13000
Fetched 1000 bars, Total: 14000
Fetched 1000 bars, Total: 15000
Fetched 1000 bars, Total: 16000
Fetched 1000 bars, Total: 17000
Fetched 1000 bars, Total: 18000
Fetched 1000 bars, Total: 19000
Fetched 1000 bars, Total: 20000
Fetched 1000 bars, Total: 21000
Fetched 1000 bars, Total: 22000
Fetched 1000 bars, Total: 23000
Fetched 1000 bars, Total: 24000
Fetched 1000 bars, Total: 25000
Fetched 1000 bars, Total: 26000
Fetched 1000 bars, Total: 27000
Fetched 1000 bars, Total: 28000
Fetched 1000 bars, Total: 29000
Fetched 1000 bars, Total: 30000
Fetched 1000 bars, Total: 31000
Fetched 1000 bars

In [3]:
df

timestamp     open     high      low    close     volume  \
49    2024-12-30 01:39:00  0.32274  0.32279  0.32127  0.32159  1567285.0   
50    2024-12-30 01:40:00  0.32160  0.32199  0.32143  0.32179   427601.0   
51    2024-12-30 01:41:00  0.32179  0.32195  0.32084  0.32135  1576400.0   
52    2024-12-30 01:42:00  0.32134  0.32138  0.32075  0.32100   598641.0   
53    2024-12-30 01:43:00  0.32101  0.32103  0.31980  0.32042  5841189.0   
...                   ...      ...      ...      ...      ...        ...   
99995 2025-03-09 11:25:00  0.18567  0.18571  0.18549  0.18561   351831.0   
99996 2025-03-09 11:26:00  0.18562  0.18566  0.18554  0.18554   220395.0   
99997 2025-03-09 11:27:00  0.18555  0.18577  0.18555  0.18576   539376.0   
99998 2025-03-09 11:28:00  0.18577  0.18587  0.18570  0.18570   416042.0   
99999 2025-03-09 11:29:00  0.18571  0.18574  0.18563  0.18571   129001.0   

         SMA_20    SMA_50    EMA_20     RSI_14      MACD  MACD_Signal  \
49     0.320182  0.317874  0.320315  67.101122  0.001301     0.001178   
50     0.320360  0.318004  0.320456  68.277920  0.001258     0.001194   
51     0.320484  0.318110  0.320541  62.943591  0.001175     0.001190   
52     0.320599  0.318193  0.320584  58.995234  0.001068     0.001166   
53     0.320681  0.318271  0.320569  53.055832  0.000927     0.001118   
...         ...       ...       ...        ...       ...          ...   
99995  0.185482  0.185303  0.185492  53.290051  0.000103     0.000081   
99996  0.185502  0.185295  0.185496  51.626026  0.000093     0.000084   
99997  0.185521  0.185296  0.185521  56.249862  0.000102     0.000087   
99998  0.185532  0.185293  0.185538  54.713828  0.000103     0.000090   
99999  0.185548  0.185288  0.185555  54.934707  0.000103     0.000093   

         ATR_14  
49     0.000767  
50     0.000752  
51     0.000777  
52     0.000767  
53     0.000800  
...         ...  
99995  0.000318  
99996  0.000304  
99997  0.000298  
99998  0.000289  
99999  0.000276  

[99951 rows x 13 columns]

In [4]:
def detect_trend(df):
    # Ensure there is enough data
    if len(df) < 50:
        print("Not enough data to determine trend.")
        return None

    # Moving Averages
    ma_bullish = df["SMA_20"].iloc[-1] > df["SMA_50"].iloc[-1]
    ma_bearish = df["SMA_20"].iloc[-1] < df["SMA_50"].iloc[-1]

    # MACD
    macd_bullish = df["MACD"].iloc[-1] > df["MACD_Signal"].iloc[-1]
    macd_bearish = df["MACD"].iloc[-1] < df["MACD_Signal"].iloc[-1]

    # RSI
    rsi_bullish = df["RSI_14"].iloc[-1] > 55
    rsi_bearish = df["RSI_14"].iloc[-1] < 45

    # ATR (Volatility Strength)
    atr_bullish = df["ATR_14"].iloc[-1] > df["ATR_14"].rolling(10).mean().iloc[-1]
    atr_bearish = df["ATR_14"].iloc[-1] < df["ATR_14"].rolling(10).mean().iloc[-1]

    # Count bullish & bearish signals
    bullish_signals = sum([ma_bullish, macd_bullish, rsi_bullish, atr_bullish])
    bearish_signals = sum([ma_bearish, macd_bearish, rsi_bearish, atr_bearish])

    # Determine final trend
    if bullish_signals >= 3:
        trend = "Bullish"
    elif bearish_signals >= 3:
        trend = "Bearish"
    else:
        trend = "Sideways / Neutral"

    print(f"Market Trend: {trend} (Bullish signals: {bullish_signals}, Bearish signals: {bearish_signals})")
    return trend

# Example usage:
trend_results = []

for i in range(50, len(df)):  # Start from 50 to ensure enough historical data
    trend_results.append(detect_trend(df.iloc[:i]))  # Run trend detection on past data

# Add the trend results as a new column
df = df.iloc[50:].copy()  # Trim the first 50 rows to match trend output
df["Trend"] = trend_results

Market Trend: Bearish (Bullish signals: 0, Bearish signals: 4)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 1)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 1)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 2

Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 1)
Market Trend: Sideways / Neutral (Bull

Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 1)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 1)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 

Market Trend: Bearish (Bullish signals: 0, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 0, Bearish signals: 4)
Market Trend: Bearish (Bullish signals: 0, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Bullish (Bullish signals: 3, Bearish signals: 1)
Market Trend: Bullish (Bullish signals: 3, Bearish signals: 1)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish s

Market Trend: Bullish (Bullish signals: 4, Bearish signals: 0)
Market Trend: Bullish (Bullish signals: 4, Bearish signals: 0)
Market Trend: Bullish (Bullish signals: 4, Bearish signals: 0)
Market Trend: Bullish (Bullish signals: 4, Bearish signals: 0)
Market Trend: Bullish (Bullish signals: 3, Bearish signals: 0)
Market Trend: Bullish (Bullish signals: 3, Bearish signals: 0)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 1)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 1)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Bearish (Bullish

...

Market Trend: Bearish (Bullish signals: 0, Bearish signals: 4)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 0, Bearish signals: 4)
Market Trend: Bearish (Bullish signals: 0, Bearish signals: 4)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 0, Bearish signals: 4)
Market Trend: Bearish (Bullish signals: 0, Bearish signals: 4)
Market Trend: Bearish (Bullish signals: 0, Bearish signals: 4)
Market Trend: Bearish (Bullish signals: 0, Bearish signals: 4)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish sign

Market Trend: Bullish (Bullish signals: 4, Bearish signals: 0)
Market Trend: Bullish (Bullish signals: 4, Bearish signals: 0)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 2)
Market Trend: Bullish (Bullish signals: 3, Bearish signals: 1)
Market Trend: Bullish (Bullish signals: 3, Bearish signals: 1)
Market T

Market Trend: Bearish (Bullish signals: 0, Bearish signals: 4)
Market Trend: Bearish (Bullish signals: 0, Bearish signals: 4)
Market Trend: Bearish (Bullish signals: 0, Bearish signals: 4)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish sign

Market Trend: Bearish (Bullish signals: 0, Bearish signals: 4)
Market Trend: Bearish (Bullish signals: 0, Bearish signals: 4)
Market Trend: Bearish (Bullish signals: 0, Bearish signals: 4)
Market Trend: Bearish (Bullish signals: 0, Bearish signals: 4)
Market Trend: Bearish (Bullish signals: 0, Bearish signals: 4)
Market Trend: Bearish (Bullish signals: 0, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 0, Bearish signals: 4)
Market Trend: Bearish (Bullish signals: 0, Bearish signals: 4)
Market Trend: Sideways / Neutral (Bullish signals: 1, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 1)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 1)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 2)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 0, Bearish signals: 4)
Market Tren

Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 0, Bearish signals: 4)
Market Trend: Bearish (Bullish signals: 0, Bearish signals: 4)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 2)
Market Trend: Sideways / Neutral (Bullish signals: 2, Bearish signals: 2)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish signals: 1, Bearish signals: 3)
Market Trend: Bearish (Bullish si

In [5]:
csv_filename = "DOGE.csv"
df.to_csv(csv_filename, index=False)